In [1]:
import numpy as np

import MDAnalysis as mda
from MDAnalysis.analysis import encore
from MDAnalysis.analysis.encore.clustering import ClusteringMethod as clm
from MDAnalysis.analysis import align


/home/user/anaconda3/envs/Xponge/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/user/anaconda3/envs/Xponge/lib/python3.12/site-packages/Bio/Application/__init__.py:39: BiopythonDeprecationWarning: The Bio.Application modules and modules relying on it have been deprecated.

Due to the on going maintenance burden of keeping command line application
wrappers up to date, we have decided to deprecate and eventually remove these
modules.

We instead now recommend building your command line and invoking it directly
with the subprocess module.
  warnings.warn(


In [2]:
import os
import glob


path = 'pdbs'
clustered_pdb_list = []
clustered_pdb_dict = {}
index_list = []
for filename in glob.glob(path + '/' + '*.pdb'):
    clustered_pdb_dict[filename.split('.')[0].split('_')[-1]] = filename
    index_list.append(int(filename.split('.')[0].split('_')[-1]))

print("Files and directories in '", path, "' :")

index_list.sort()
for i in range(len(index_list)):
    clustered_pdb_list.append(clustered_pdb_dict[str(index_list[i])])

# prints all files
print(clustered_pdb_dict)
print(clustered_pdb_list)
print(len(clustered_pdb_list))

clustered_pdb_list = ['./' + i for i in clustered_pdb_list]
print(clustered_pdb_list)
print(len(clustered_pdb_list))


Files and directories in ' pdbs ' :
{'23721': 'pdbs/8qw7_A_docked_final_23721.pdb', '5313': 'pdbs/8qw7_A_docked_final_5313.pdb', '19922': 'pdbs/8qw7_A_docked_final_19922.pdb', '27203': 'pdbs/8qw7_A_docked_final_27203.pdb', '31304': 'pdbs/8qw7_A_docked_final_31304.pdb', '10943': 'pdbs/8qw7_A_docked_final_10943.pdb', '5983': 'pdbs/8qw7_A_docked_final_5983.pdb', '3328': 'pdbs/8qw7_A_docked_final_3328.pdb', '12585': 'pdbs/8qw7_A_docked_final_12585.pdb', '11120': 'pdbs/8qw7_A_docked_final_11120.pdb', '5640': 'pdbs/8qw7_A_docked_final_5640.pdb', '18410': 'pdbs/8qw7_A_docked_final_18410.pdb', '24183': 'pdbs/8qw7_A_docked_final_24183.pdb', '24022': 'pdbs/8qw7_A_docked_final_24022.pdb', '10225': 'pdbs/8qw7_A_docked_final_10225.pdb', '22872': 'pdbs/8qw7_A_docked_final_22872.pdb', '19494': 'pdbs/8qw7_A_docked_final_19494.pdb', '10076': 'pdbs/8qw7_A_docked_final_10076.pdb', '28121': 'pdbs/8qw7_A_docked_final_28121.pdb', '25357': 'pdbs/8qw7_A_docked_final_25357.pdb', '31302': 'pdbs/8qw7_A_docked_fi

In [3]:

clustered_traj = mda.Universe('8qw7_A.pdb', clustered_pdb_list)

print(len(clustered_traj.trajectory))

ref_for_traj = mda.Universe('8qw7_A.pdb', '8qw7_A.pdb')

E3_origin = mda.Universe('8qw7_B.pdb', 'pstruct_transformed.pdb')
ref_for_E3 = mda.Universe('8qw7_B.pdb', '8qw7_B.pdb')


/home/user/anaconda3/envs/Xponge/lib/python3.12/site-packages/MDAnalysis/coordinates/base.py:725: UserWarning: Reader has no dt information, set to 1.0 ps
  return self.ts.dt


33120


In [4]:
# E3 is receptor, and POI is ligand.
ref_for_E3_com = ref_for_E3.atoms.center(weights=None)
print(ref_for_E3.select_atoms('name CA').positions[0:3,:])
ref_for_E3.atoms.translate(-ref_for_E3_com)
print(ref_for_E3.select_atoms('name CA').positions[0:3,:])

E3_origin_com = E3_origin.atoms.center(weights=None)
print(E3_origin.select_atoms('name CA').positions[0:3,:])
E3_origin.atoms.translate(-E3_origin_com)
print(E3_origin.select_atoms('name CA').positions[0:3,:])

ref_for_E3.atoms.write("E3_ref_translated_1.pdb")
E3_origin.atoms.write("E3_origin_translated_1.pdb")

R = align.rotation_matrix(E3_origin.select_atoms('name CA').positions,
                          ref_for_E3.select_atoms('name CA').positions)[0]

print(R)


E3_origin_backup = E3_origin.copy()

with mda.Writer('aligned.pdb', clustered_traj.atoms.n_atoms) as w:
    for ts in clustered_traj.trajectory:

        print(ts.frame)
        #print(clustered_traj.select_atoms('name CA').positions[0:3,:])

        clustered_traj.atoms.translate(-E3_origin_com)
        #clustered_traj.atoms.write("POI_translated_1.pdb")

        clustered_traj.atoms.rotate(R)
        E3_origin.atoms.rotate(R)
        #clustered_traj.atoms.write("POI_translated_2.pdb")
        #E3_origin.atoms.write("E3_translated_2.pdb")

        #print(clustered_traj.select_atoms('name CA').positions[0:3,:])

        clustered_traj.atoms.translate(ref_for_E3_com)
        #clustered_traj.atoms.write("POI_translated_3.pdb")

        #print(clustered_traj.select_atoms('name CA').positions[0:3,:])

        #POI_origin.atoms.write("rotated.pdb")
        w.write(clustered_traj.atoms)

        #break


[[23.579 42.334  7.923]
 [21.98  38.917  8.227]
 [18.264 38.561  8.724]]
[[ 5.5633636  19.50497    -7.2461205 ]
 [ 3.9643626  16.08797    -6.94212   ]
 [ 0.24836302 15.731972   -6.4451203 ]]
[[69.334 85.105 58.608]
 [67.734 81.688 58.912]
 [64.019 81.332 59.409]]
[[ 5.5638447  19.505283   -7.2463665 ]
 [ 3.9638462  16.088284   -6.9423695 ]
 [ 0.24884224 15.732282   -6.445368  ]]
[[ 1.00000000e+00 -2.99593168e-06  2.56689824e-06]
 [ 2.99592430e-06  1.00000000e+00  2.87408016e-06]
 [-2.56690685e-06 -2.87407247e-06  1.00000000e+00]]


/home/user/anaconda3/envs/Xponge/lib/python3.12/site-packages/MDAnalysis/coordinates/PDB.py:777: UserWarning: Unit cell dimensions not found. CRYST1 record set to unitary values.
  warnings.warn("Unit cell dimensions not found. "


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27